### PROBLEM STATEMENT-TO PREDICT SPECIES
### DEPENDENT VARIABLE - 'SPECIES'

## LOGISTIC REGRESSION:

### IMPORT LIBRARIES

In [1]:
import pandas as pd
import numpy as np

from sklearn.linear_model import LogisticRegression,RidgeClassifier
from sklearn.model_selection import train_test_split,GridSearchCV,RandomizedSearchCV

from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from sklearn.metrics import roc_auc_score,roc_curve,precision_score,recall_score,f1_score

import matplotlib.pyplot as plt
import seaborn as sns

import warnings
warnings.filterwarnings('ignore')

### DATA GATHERING

In [2]:
df=pd.read_csv('iris.csv')
df

Id  SepalLengthCm  SepalWidthCm  PetalLengthCm  PetalWidthCm  \
0      1            5.1           3.5            1.4           0.2   
1      2            4.9           3.0            1.4           0.2   
2      3            4.7           3.2            1.3           0.2   
3      4            4.6           3.1            1.5           0.2   
4      5            5.0           3.6            1.4           0.2   
..   ...            ...           ...            ...           ...   
145  146            6.7           3.0            5.2           2.3   
146  147            6.3           2.5            5.0           1.9   
147  148            6.5           3.0            5.2           2.0   
148  149            6.2           3.4            5.4           2.3   
149  150            5.9           3.0            5.1           1.8   

            Species  
0       Iris-setosa  
1       Iris-setosa  
2       Iris-setosa  
3       Iris-setosa  
4       Iris-setosa  
..              ...  
145  Iris-virginica  
146  Iris-virginica  
147  Iris-virginica  
148  Iris-virginica  
149  Iris-virginica  

[150 rows x 6 columns]

### EDA & FEATURE ENGINEERING:

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150 entries, 0 to 149
Data columns (total 6 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Id             150 non-null    int64  
 1   SepalLengthCm  150 non-null    float64
 2   SepalWidthCm   150 non-null    float64
 3   PetalLengthCm  150 non-null    float64
 4   PetalWidthCm   150 non-null    float64
 5   Species        150 non-null    object 
dtypes: float64(4), int64(1), object(1)
memory usage: 7.2+ KB


In [4]:
df.isna().mean()*100

Id               0.0
SepalLengthCm    0.0
SepalWidthCm     0.0
PetalLengthCm    0.0
PetalWidthCm     0.0
Species          0.0
dtype: float64

In [5]:
df.drop('Id',axis=1,inplace=True)

### TRAIN TEST SPLIT:

In [6]:
x=df.drop('Species',axis=1)
y=df['Species']

In [7]:
x_train,x_test,y_train,y_test=train_test_split(x,y,test_size=0.2,random_state=10,stratify=y)
y_train

123     Iris-virginica
92     Iris-versicolor
60     Iris-versicolor
11         Iris-setosa
121     Iris-virginica
            ...       
114     Iris-virginica
14         Iris-setosa
128     Iris-virginica
19         Iris-setosa
61     Iris-versicolor
Name: Species, Length: 120, dtype: object

### MODEL TRAIN:

In [8]:
model_log_clf=LogisticRegression(multi_class='ovr')
model_log_clf.fit(x_train,y_train)


LogisticRegression(multi_class='ovr')

In [9]:
y_test.value_counts()

Iris-versicolor    10
Iris-setosa        10
Iris-virginica     10
Name: Species, dtype: int64

### MODEL EVALUATION:

In [10]:
df_eval=pd.DataFrame(columns=['name','accuracy_score'])
df_eval

Empty DataFrame
Columns: [name, accuracy_score]
Index: []

In [11]:
def evalution(model_logistic_clf,x_train,y_train,name):

    y_train_pre = model_logistic_clf.predict(x_train)

    accuracy_score_train =accuracy_score(y_train,y_train_pre)

    # class-1
#     precision_score_train_1=precision_score(y_train,y_train_pre)
#     precision_score_train_1


#     recall_score_train_1=recall_score(y_train,y_train_pre)
#     recall_score_train_1

#     f1_score_train_1 = f1_score(y_train,y_train_pre)
#     f1_score_train_1

    # Class - 0
#     precision_score_train_0=precision_score(y_train,y_train_pre,pos_label=0)
#     precision_score_train_0


#     recall_score_train_0=recall_score(y_train,y_train_pre,pos_label=0)
#     recall_score_train_0

#     f1_score_train_0 = f1_score(y_train,y_train_pre,pos_label=0)
#     f1_score_train_0
    
    row_2 = {'name':[name],'accuracy_score'  : [accuracy_score_train]}
    df_eval_1 = pd.DataFrame(row_2)
    global df_eval 
    # df_eval.append(df_eval_1)
    df_eval=pd.concat([df_eval,df_eval_1],ignore_index=True)
    

In [12]:
evalution(model_log_clf,x_train,y_train,'model_log_clf_train')

In [13]:
evalution(model_log_clf,x_test,y_test,'model_log_clf_test')

In [14]:
df_eval

name  accuracy_score
0  model_log_clf_train        0.941667
1   model_log_clf_test        1.000000

# RIDGE CLASSIFIER:

### MODEL TRAIN

In [15]:
ridge_model_clf=RidgeClassifier(alpha=1.0)
ridge_model_clf.fit(x_train,y_train)

RidgeClassifier()

### MODEL EVALUATION:

In [16]:
evalution(ridge_model_clf,x_train,y_train,'ridge_model_clf_train')

In [17]:
evalution(ridge_model_clf,x_test,y_test,'ridge_model_clf_test')

In [18]:
df_eval

name  accuracy_score
0    model_log_clf_train        0.941667
1     model_log_clf_test        1.000000
2  ridge_model_clf_train        0.825000
3   ridge_model_clf_test        0.966667

### HYPER PARAMETER TUNING RIDGE CLASSIFIER:

In [19]:
ridge_model_clf_hyp=RidgeClassifier()
hyperparameter_grid={'alpha':np.arange(0.05,1.1,0.001)}

gscv_ridge_model=GridSearchCV(ridge_model_clf_hyp,hyperparameter_grid,cv=5)
gscv_ridge_model.fit(x_train,y_train)
gscv_ridge_model.best_estimator_


RidgeClassifier(alpha=0.8690000000000008)

In [20]:
ridge_model_clf_hyp=gscv_ridge_model.best_estimator_
ridge_model_clf_hyp.fit(x_train,y_train)

RidgeClassifier(alpha=0.8690000000000008)

### MODEL EVALUATION:

In [21]:
evalution(ridge_model_clf_hyp,x_train,y_train,'ridge_model_clf_hyp_train')

In [22]:
evalution(ridge_model_clf_hyp,x_test,y_test,'ridge_model_clf_hyp_test')

In [23]:
df_eval

name  accuracy_score
0        model_log_clf_train        0.941667
1         model_log_clf_test        1.000000
2      ridge_model_clf_train        0.825000
3       ridge_model_clf_test        0.966667
4  ridge_model_clf_hyp_train        0.825000
5   ridge_model_clf_hyp_test        0.966667

# KNN CLASSIFIER:

In [24]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.preprocessing import MinMaxScaler,StandardScaler

In [25]:
df_knn=df.copy()

In [26]:
df_knn

SepalLengthCm  SepalWidthCm  PetalLengthCm  PetalWidthCm         Species
0              5.1           3.5            1.4           0.2     Iris-setosa
1              4.9           3.0            1.4           0.2     Iris-setosa
2              4.7           3.2            1.3           0.2     Iris-setosa
3              4.6           3.1            1.5           0.2     Iris-setosa
4              5.0           3.6            1.4           0.2     Iris-setosa
..             ...           ...            ...           ...             ...
145            6.7           3.0            5.2           2.3  Iris-virginica
146            6.3           2.5            5.0           1.9  Iris-virginica
147            6.5           3.0            5.2           2.0  Iris-virginica
148            6.2           3.4            5.4           2.3  Iris-virginica
149            5.9           3.0            5.1           1.8  Iris-virginica

[150 rows x 5 columns]

### SCALING-NORMALIZATION:

In [27]:
x = df_knn.drop('Species',axis = 1)

normal_scaler = MinMaxScaler()
normal_scaler.fit(x)

normalized_array = normal_scaler.transform(x)
x_df = pd.DataFrame(normalized_array,columns=x.columns)
x_df

SepalLengthCm  SepalWidthCm  PetalLengthCm  PetalWidthCm
0         0.222222      0.625000       0.067797      0.041667
1         0.166667      0.416667       0.067797      0.041667
2         0.111111      0.500000       0.050847      0.041667
3         0.083333      0.458333       0.084746      0.041667
4         0.194444      0.666667       0.067797      0.041667
..             ...           ...            ...           ...
145       0.666667      0.416667       0.711864      0.916667
146       0.555556      0.208333       0.677966      0.750000
147       0.611111      0.416667       0.711864      0.791667
148       0.527778      0.583333       0.745763      0.916667
149       0.444444      0.416667       0.694915      0.708333

[150 rows x 4 columns]

### TRAIN TEST SPLIT:

In [28]:
y=df['Species']

In [29]:
x_train, x_test, y_train, y_test = train_test_split(x_df,y,test_size=0.2,random_state=10,stratify=y)

In [30]:
#x_test

### MODEL TRAIN:

In [31]:
model_knn_clf=KNeighborsClassifier(n_neighbors=5)
model_knn_clf.fit(x_train,y_train)

KNeighborsClassifier()

In [32]:
evalution(model_knn_clf,x_train,y_train,'model_knn_clf_train_norm')

In [33]:
evalution(model_knn_clf,x_test,y_test,'model_knn_clf_test_norm')

In [34]:
df_eval

name  accuracy_score
0        model_log_clf_train        0.941667
1         model_log_clf_test        1.000000
2      ridge_model_clf_train        0.825000
3       ridge_model_clf_test        0.966667
4  ridge_model_clf_hyp_train        0.825000
5   ridge_model_clf_hyp_test        0.966667
6   model_knn_clf_train_norm        0.950000
7    model_knn_clf_test_norm        1.000000

### SCALING-STANDARDIZATION:

In [35]:
x = df_knn.drop('Species',axis = 1)

std_scaler = StandardScaler()
std_scaler.fit(x)

standardised_array = std_scaler.transform(x)
x_df1 = pd.DataFrame(standardised_array,columns=x.columns)
x_df1

SepalLengthCm  SepalWidthCm  PetalLengthCm  PetalWidthCm
0        -0.900681      1.032057      -1.341272     -1.312977
1        -1.143017     -0.124958      -1.341272     -1.312977
2        -1.385353      0.337848      -1.398138     -1.312977
3        -1.506521      0.106445      -1.284407     -1.312977
4        -1.021849      1.263460      -1.341272     -1.312977
..             ...           ...            ...           ...
145       1.038005     -0.124958       0.819624      1.447956
146       0.553333     -1.281972       0.705893      0.922064
147       0.795669     -0.124958       0.819624      1.053537
148       0.432165      0.800654       0.933356      1.447956
149       0.068662     -0.124958       0.762759      0.790591

[150 rows x 4 columns]

### TRAIN TEST SPLIT:

In [36]:
y=df['Species']

In [37]:
x_train, x_test, y_train, y_test = train_test_split(x_df1,y,test_size=0.2,random_state=10,stratify=y)

### MODEL TRAIN:

In [38]:
model_knn_clf_std=KNeighborsClassifier(n_neighbors=5)
model_knn_clf_std.fit(x_train,y_train)

KNeighborsClassifier()

### MODEL EVALUATION:

In [39]:
evalution(model_knn_clf_std,x_train,y_train,'model_knn_clf_train_std')

In [40]:
evalution(model_knn_clf_std,x_test,y_test,'model_knn_clf_test_std')

In [41]:
df_eval

name  accuracy_score
0        model_log_clf_train        0.941667
1         model_log_clf_test        1.000000
2      ridge_model_clf_train        0.825000
3       ridge_model_clf_test        0.966667
4  ridge_model_clf_hyp_train        0.825000
5   ridge_model_clf_hyp_test        0.966667
6   model_knn_clf_train_norm        0.950000
7    model_knn_clf_test_norm        1.000000
8    model_knn_clf_train_std        0.950000
9     model_knn_clf_test_std        1.000000

## DECISION TREE CLASSIFIER:

In [42]:
from sklearn.tree import DecisionTreeClassifier,plot_tree


In [43]:
df

SepalLengthCm  SepalWidthCm  PetalLengthCm  PetalWidthCm         Species
0              5.1           3.5            1.4           0.2     Iris-setosa
1              4.9           3.0            1.4           0.2     Iris-setosa
2              4.7           3.2            1.3           0.2     Iris-setosa
3              4.6           3.1            1.5           0.2     Iris-setosa
4              5.0           3.6            1.4           0.2     Iris-setosa
..             ...           ...            ...           ...             ...
145            6.7           3.0            5.2           2.3  Iris-virginica
146            6.3           2.5            5.0           1.9  Iris-virginica
147            6.5           3.0            5.2           2.0  Iris-virginica
148            6.2           3.4            5.4           2.3  Iris-virginica
149            5.9           3.0            5.1           1.8  Iris-virginica

[150 rows x 5 columns]

### TRAIN TEST SPLIT:

In [44]:
x_train,x_test,y_train,y_test=train_test_split(x,y,test_size=0.2,random_state=10,stratify=y)

### MODEL TRAIN:

In [45]:
model_dt_clf=DecisionTreeClassifier(random_state=20)
model_dt_clf.fit(x_train,y_train)

DecisionTreeClassifier(random_state=20)

### MODEL EVALUATION:

In [46]:
evalution(model_dt_clf,x_train,y_train,'model_dt_clf_train')

In [47]:
evalution(model_dt_clf,x_test,y_test,'model_dt_clf_test')

In [48]:
df_eval

name  accuracy_score
0         model_log_clf_train        0.941667
1          model_log_clf_test        1.000000
2       ridge_model_clf_train        0.825000
3        ridge_model_clf_test        0.966667
4   ridge_model_clf_hyp_train        0.825000
5    ridge_model_clf_hyp_test        0.966667
6    model_knn_clf_train_norm        0.950000
7     model_knn_clf_test_norm        1.000000
8     model_knn_clf_train_std        0.950000
9      model_knn_clf_test_std        1.000000
10         model_dt_clf_train        1.000000
11          model_dt_clf_test        0.966667

In [49]:
### PLOT DECISION TREE:

In [50]:
plt.figure(figsize=(200,160))
plot_tree(model_dt_clf,feature_names=x.columns,class_names=['0','1','2'],filled=True)
plt.savefig('DT_CLF.pdf')

### DECISION TREE CLASSIFIER WITH HYPERPARAMETER TUNING:

In [51]:
model_dt_clf_hyp=DecisionTreeClassifier(random_state=20)

hyperparameters={'criterion':['gini','entropy'],
                    'max_depth':np.arange(3,10),
                    'min_samples_split':np.arange(2,20),
                    'min_samples_leaf':np.arange(2,10)}
gscv_dt_model=GridSearchCV(model_dt_clf,hyperparameters,cv=5)
gscv_dt_model.fit(x_train,y_train)
gscv_dt_model.best_estimator_

DecisionTreeClassifier(max_depth=3, min_samples_leaf=3, random_state=20)

In [52]:
model_dt_clf_hyp=gscv_dt_model.best_estimator_
model_dt_clf_hyp.fit(x_train,y_train)

DecisionTreeClassifier(max_depth=3, min_samples_leaf=3, random_state=20)

### MODEL EVALUATION:

In [53]:
evalution(model_dt_clf_hyp,x_train,y_train,'model_dt_clf_hyp_train')

In [54]:
evalution(model_dt_clf_hyp,x_test,y_test,'model_dt_clf_hyp_test')

In [55]:
df_eval

name  accuracy_score
0         model_log_clf_train        0.941667
1          model_log_clf_test        1.000000
2       ridge_model_clf_train        0.825000
3        ridge_model_clf_test        0.966667
4   ridge_model_clf_hyp_train        0.825000
5    ridge_model_clf_hyp_test        0.966667
6    model_knn_clf_train_norm        0.950000
7     model_knn_clf_test_norm        1.000000
8     model_knn_clf_train_std        0.950000
9      model_knn_clf_test_std        1.000000
10         model_dt_clf_train        1.000000
11          model_dt_clf_test        0.966667
12     model_dt_clf_hyp_train        0.966667
13      model_dt_clf_hyp_test        1.000000

### PLOT DT AFTER HYPERPARAMETER TUNING:

In [56]:
plt.figure(figsize=(200,160))
plot_tree(model_dt_clf_hyp, feature_names=x.columns,class_names=['0','1','2'],filled=True)
plt.savefig('DecisionTree_hyp.pdf')

# RANDOM FOREST CLASSIFIER:

In [57]:
from sklearn.ensemble import RandomForestClassifier

### MODEL TRAIN:

In [58]:
model_rf_clf=RandomForestClassifier(random_state=10)
model_rf_clf.fit(x_train,y_train)

RandomForestClassifier(random_state=10)

### MODEL EVALUATION:

In [59]:
evalution(model_rf_clf,x_train,y_train,'model_rf_clf_train')

In [60]:
evalution(model_rf_clf,x_test,y_test,'model_rf_clf_test')

In [61]:
df_eval

name  accuracy_score
0         model_log_clf_train        0.941667
1          model_log_clf_test        1.000000
2       ridge_model_clf_train        0.825000
3        ridge_model_clf_test        0.966667
4   ridge_model_clf_hyp_train        0.825000
5    ridge_model_clf_hyp_test        0.966667
6    model_knn_clf_train_norm        0.950000
7     model_knn_clf_test_norm        1.000000
8     model_knn_clf_train_std        0.950000
9      model_knn_clf_test_std        1.000000
10         model_dt_clf_train        1.000000
11          model_dt_clf_test        0.966667
12     model_dt_clf_hyp_train        0.966667
13      model_dt_clf_hyp_test        1.000000
14         model_rf_clf_train        1.000000
15          model_rf_clf_test        1.000000

### RANDOM FOREST WITH HYPERPARAMETER TUNING:

In [62]:
model_rf_clf_hyp=RandomForestClassifier(random_state=10)

hyp = {
    "n_estimators":np.arange(10,200),
    "criterion": ['gini','entropy'],
    "max_depth" : np.arange(5,15),
    "min_samples_split":np.arange(5,20),
    "min_samples_leaf":np.arange(4,15),
    "max_features":['auto']
}

rscv_rf_clf = RandomizedSearchCV(model_rf_clf_hyp, hyp, cv = 6)
rscv_rf_clf.fit(x_train,y_train)
rscv_rf_clf.best_estimator_

RandomForestClassifier(max_depth=14, min_samples_leaf=4, min_samples_split=7,
                       n_estimators=19, random_state=10)

In [63]:
model_rf_clf_hyp=rscv_rf_clf.best_estimator_
model_rf_clf_hyp.fit(x_train,y_train)

RandomForestClassifier(max_depth=14, min_samples_leaf=4, min_samples_split=7,
                       n_estimators=19, random_state=10)

### MODEL EVALUATION:

In [64]:
evalution(model_rf_clf_hyp,x_train,y_train,'model_rf_clf_hyp_train')

In [65]:
evalution(model_rf_clf_hyp,x_test,y_test,'model_rf_clf_hyp_test')

In [66]:
df_eval

name  accuracy_score
0         model_log_clf_train        0.941667
1          model_log_clf_test        1.000000
2       ridge_model_clf_train        0.825000
3        ridge_model_clf_test        0.966667
4   ridge_model_clf_hyp_train        0.825000
5    ridge_model_clf_hyp_test        0.966667
6    model_knn_clf_train_norm        0.950000
7     model_knn_clf_test_norm        1.000000
8     model_knn_clf_train_std        0.950000
9      model_knn_clf_test_std        1.000000
10         model_dt_clf_train        1.000000
11          model_dt_clf_test        0.966667
12     model_dt_clf_hyp_train        0.966667
13      model_dt_clf_hyp_test        1.000000
14         model_rf_clf_train        1.000000
15          model_rf_clf_test        1.000000
16     model_rf_clf_hyp_train        0.958333
17      model_rf_clf_hyp_test        1.000000

## ADABOOST CLASSIFIER:

In [67]:
from sklearn.ensemble import AdaBoostClassifier

### MODEL TRAINING:

In [68]:
adb_clf=AdaBoostClassifier(random_state=20)
adb_clf.fit(x_train,y_train)

AdaBoostClassifier(random_state=20)

### MODEL EVALUATION:

In [69]:
evalution(adb_clf,x_train,y_train,'adb_clf_train')

In [70]:
evalution(adb_clf,x_test,y_test,'adb_clf_test')

In [71]:
df_eval

name  accuracy_score
0         model_log_clf_train        0.941667
1          model_log_clf_test        1.000000
2       ridge_model_clf_train        0.825000
3        ridge_model_clf_test        0.966667
4   ridge_model_clf_hyp_train        0.825000
5    ridge_model_clf_hyp_test        0.966667
6    model_knn_clf_train_norm        0.950000
7     model_knn_clf_test_norm        1.000000
8     model_knn_clf_train_std        0.950000
9      model_knn_clf_test_std        1.000000
10         model_dt_clf_train        1.000000
11          model_dt_clf_test        0.966667
12     model_dt_clf_hyp_train        0.966667
13      model_dt_clf_hyp_test        1.000000
14         model_rf_clf_train        1.000000
15          model_rf_clf_test        1.000000
16     model_rf_clf_hyp_train        0.958333
17      model_rf_clf_hyp_test        1.000000
18              adb_clf_train        0.950000
19               adb_clf_test        1.000000

### ADABOOST WITH HYPERPARAMETER TUNING:

In [72]:
adb_clf_hyp=AdaBoostClassifier(random_state=20)

param_grid={'n_estimators':np.arange(10,100),
            'learning_rate':np.arange(0.01,1,0.01)
           }

rscv_adb_model=RandomizedSearchCV(adb_clf_hyp,param_grid,cv=7)
rscv_adb_model.fit(x_train,y_train)
rscv_adb_model.best_estimator_

AdaBoostClassifier(learning_rate=0.92, n_estimators=43, random_state=20)

In [73]:
adb_clf_hyp=rscv_adb_model.best_estimator_
adb_clf_hyp.fit(x_train,y_train)

AdaBoostClassifier(learning_rate=0.92, n_estimators=43, random_state=20)

### MODEL EVALUATION:

In [74]:
evalution(adb_clf_hyp,x_train,y_train,'adb_clf_hyp_train')

In [75]:
evalution(adb_clf_hyp,x_test,y_test,'adb_clf_hyp_test')

In [76]:
df_eval

name  accuracy_score
0         model_log_clf_train        0.941667
1          model_log_clf_test        1.000000
2       ridge_model_clf_train        0.825000
3        ridge_model_clf_test        0.966667
4   ridge_model_clf_hyp_train        0.825000
5    ridge_model_clf_hyp_test        0.966667
6    model_knn_clf_train_norm        0.950000
7     model_knn_clf_test_norm        1.000000
8     model_knn_clf_train_std        0.950000
9      model_knn_clf_test_std        1.000000
10         model_dt_clf_train        1.000000
11          model_dt_clf_test        0.966667
12     model_dt_clf_hyp_train        0.966667
13      model_dt_clf_hyp_test        1.000000
14         model_rf_clf_train        1.000000
15          model_rf_clf_test        1.000000
16     model_rf_clf_hyp_train        0.958333
17      model_rf_clf_hyp_test        1.000000
18              adb_clf_train        0.950000
19               adb_clf_test        1.000000
20          adb_clf_hyp_train        0.950000
21           adb_clf_hyp_test        0.966667

## PICKLE FILE FOR RANDOM FOREST

In [ ]:
import pickle

with open('iris_model_rf','wb') as f:
    f.write()